# Project : Steam's videogames platform

In [ ]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [ ]:
# Library imports for project analysis
from pyspark.sql import functions as F 
from functools import reduce
from pyspark.sql.functions import col, mean, size, split, explode, count, desc, max, sum
from pyspark.sql.types import IntegerType
from operator import add
from pyspark.sql.window import Window
import pandas as pd
import numpy as np

In [ ]:
# Reading the json file
filepath = "s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json"
dataset = (spark.read.format('json').option('header', 'true').option('inferSchema', 'true').load(filepath))

In [ ]:
type(dataset)

Out[5]: pyspark.sql.dataframe.DataFrame

In [ ]:
# Structure of Dataset
dataset.printSchema()

root
 |-- data: struct (nullable = true)
 |    |-- appid: long (nullable = true)
 |    |-- categories: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- ccu: long (nullable = true)
 |    |-- developer: string (nullable = true)
 |    |-- discount: string (nullable = true)
 |    |-- genre: string (nullable = true)
 |    |-- header_image: string (nullable = true)
 |    |-- initialprice: string (nullable = true)
 |    |-- languages: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- negative: long (nullable = true)
 |    |-- owners: string (nullable = true)
 |    |-- platforms: struct (nullable = true)
 |    |    |-- linux: boolean (nullable = true)
 |    |    |-- mac: boolean (nullable = true)
 |    |    |-- windows: boolean (nullable = true)
 |    |-- positive: long (nullable = true)
 |    |-- price: string (nullable = true)
 |    |-- publisher: string (nullable = true)
 |    |-- release_date: string (nullable = true)
 |    |-

In [ ]:
# Size of dataset
dataset.count()

Out[7]: 55691

In [ ]:
dataset.select("id").distinct().count() == dataset.select("id").count()

Out[8]: True

### Analysis at the "macro" level

#### Which publisher has released the most games on Steam ?

In [ ]:
publisher_df = dataset.withColumn('publisher', F.col('data').getField('publisher'))
publisher_df = publisher_df.groupBy('publisher').count()
publisher_df = publisher_df.orderBy(publisher_df['count'].desc())
display(publisher_df)

publisher count Big Fish Games 422 8floor 202 SEGA 165 Strategy First 151 Square Enix 141 Choice of Games 140 Sekai Project 132 HH-Games 132 132 Ubisoft 127 Laush Studio 126 THQ Nordic 125 Alawar Entertainment 107 Fulqrum Publishing 104 Plug In Digital 101 Ziggurat 100 Slitherine Ltd. 99 Sokpop Collective 99 Devolver Digital 98 KOEI TECMO GAMES CO., LTD. 90 Reforged Group 89 Electronic Arts 88 Komodo 87 PLAYISM 87 SA Industry 87 Microids 84 Piece Of Voxel 81 Hosted Games 79 Kagura Games 79 Boogygames Studios 78 Artifex Mundi 75 tinyBuild 72 Daedalic Entertainment 72 Blender Games 71 BANDAI NAMCO Entertainment 69 Paradox Interactive 69 Tero Lunkka 68 2K 67 My Way Games 66 ESDigital Games 64 Garage Games 62 MAGIX Software GmbH 62 Nacon 60 Forever Entertainment S. A. 60 RewindApp 59 Ripknot Systems 55 United Independent Entertainment 55 Bethesda Softworks 55 Back To Basics Gaming 54 Hede 54 MangaGamer 53 GrabTheGames 52 William at Oxford 52 Focus Entertainment 52 Activision 51 KEMCO 51 Ghost_RUS Games 50 Aldorlea Games 50 Individual Software 49 Sometimes You 49 Trinity Project 47 Volens Nolens Games 47 玫瑰工作室 47 Iceberg Interactive 46 Droid Riot 46 Atomic Fabrik, Cristian Manolachi 46 PsychoFlux Entertainment 46 Xbox Game Studios 46 Funbox Media Ltd 45 ImperiumGame 44 NIS America, Inc. 44 PQube 44 Dnovel 43 Kalypso Media Digital 43 HexWar Games 42 Enoops 42 8Floor 41 Pixel Games UK 41 505 Games 41 Atari 40 Big Black Bear 40 HandyGames 40 Winged Cloud 40 familyplay 40 Anamik Majumdar 40 Deep Silver 38 HandMade Games 37 Team17 Digital Ltd 37 Rebellion 37 New Reality Games 37 Disney 37 kovalevviktor 37 Headup 37 Bitlock Studio 37 Zoo Corporation 36 MumboJumbo 36 Piko Interactive LLC, Bleem! 35 GameHouse 35 Milestone S.r.l. 35 Valve 35 Qumaron 35 Capcom 35 khukhrovr 35 Luci Entertainment 35 EnsenaSoft 35 Curve Games 35 Aerosoft GmbH 34 Jetdogs Studios 34 DigiPen Institute of Technology 34 KISS ltd 33 Spike Chunsoft Co., Ltd. 33 Meridian4 33 Kedexa 32 For Kids 32 Humongous Entertainment, Nightdive Studios 32 ANPA.US 32 HeR Interactive 32 Assemble Entertainment 31 Gotcha Gotcha Games 31 NanningsGames 31 Arc System Works 31 Outright Games Ltd. 31 Nightdive Studios 31 Fruitbat Factory 30 LucasArts, Lucasfilm, Disney 29 Minimol Games 29 SakuraGame 29 Warner Bros. Interactive Entertainment 29 Raw Fury 29 Louie Inc 29 橙光游戏 29 Bohemia Interactive 28 INFINITE BRIDGE 28 kazakovstudios 28 Snkl Studio 28 Good Shepherd Entertainment 28 Armor Games Studios 28 OTAKU Plan 28 Viva Media 27 EpiXR Games UG 27 Team17 27 Gamera Games 27 Winter Wolves 26 Kairosoft Co.,Ltd 26 Anatoliy Loginovskikh 26 Humble Games 26 ebi-hime 26 XSEED Games, Marvelous USA, Inc. 26 КиКо 25 KPL 25 Quarlellle 25 Grey Alien Games 25 Konami Digital Entertainment 25 Digerati 25 SNK CORPORATION 25 Henteko Doujin 25 Ratalaika Games S.L. 25 Digital Tribe 25 Freedom Games 25 Wolverine Studios 24 Jackbox Games, Inc. 24 Cute Hannah's Games 24 CFK Co., Ltd. 24 Paradise Project 24 CAPCOM Co., Ltd. 24 Versus Evil 24 Idea Factory International 24 FIVE-BN GAMES 24 Retroism, Nightdive Studios 24 Interplay Entertainment Corp. 24 Quiet River 24 Libredia 24 astragon Entertainment 24 Frontwing USA 24 MIRROR Soft 23 Annapurna Interactive 23 indie_games_studio 23 Gamenesis 23 W.T.B. 23 None 22 SOFTSTAR ENTERTAINMENT 22 Sacada 22 Warfare Studios 22 LTZinc 22 Senpai Studios 22 Phoenixxx Games 22 My Label Game Studio 22 Cosmi Valusoft 21 Alternative Software Ltd 21 RunServer 21 Cristian Manolachi, Atomic Fabrik 21 XSEED Games, Marvelous USA, Inc., Marvelous 21 No Gravity Games 21 MACKINN7 21 Dear Villagers 20 Headup Games 20 Codemasters, Electronic Arts 20 Stardock Entertainment 20 Ultimate Games S.A. 20 AFBIK Studio 20 Metal Fox 20 HIKARI FIELD 20 Telltale Games 20 Meng Games 20 Archor Games 20 Mens Sana Interactive 20 Tonguç Bodur 20 Red twice potato 20 Lovely Games 20 Rex Junior 20 DLsite 20 Casual Arts 20 PopCap Games, Inc. 19 Nicalis, Inc. 19 Enaayah Software Development and Services Private Limi

Big Fish Game is the publisher that released the most games on Steam

#### What are the best rated games ?

In [ ]:
rate_df = dataset.select('data.name', 'data.positive', 'data.negative')
rate_df = rate_df.select('*', (rate_df.positive + rate_df.negative).alias('total_ratings'))
rate_df = rate_df.select('*', (rate_df.positive / rate_df.total_ratings).alias('positive_ratings'))
rate_df.show()

+------------------------------------+--------+--------+-------------+-------------------+
|                                name|positive|negative|total_ratings|   positive_ratings|
+------------------------------------+--------+--------+-------------+-------------------+
|                      Counter-Strike|  201215|    5199|       206414| 0.9748127549487923|
|                           ASCENXION|      27|       5|           32|            0.84375|
|                         Crown Trick|    4032|     646|         4678| 0.8619067977768277|
|                Cook, Serve, Deli...|    1575|     115|         1690| 0.9319526627218935|
|                            细胞战争|       0|       1|            1|                0.0|
|                             Zengeon|    1018|     462|         1480| 0.6878378378378378|
|干支セトラ　陽ノ卷｜干支etc.　陽之卷|      18|       6|           24|               0.75|
|            Jumping Master(跳跳大咖)|      50|      34|           84| 0.5952380952380952|
|                      

In [ ]:
mean_ratings = rate_df.agg(F.mean('total_ratings')).collect()[0][0]
mean_ratings

Out[11]: 1712.7132929916863

In [ ]:
rate_df = rate_df.filter(rate_df.total_ratings > mean_ratings).orderBy(rate_df['positive_ratings'].desc()).limit(100)
display(rate_df)

name positive negative total_ratings positive_ratings Aventura Copilului Albastru și Urât 2203 14 2217 0.9936851601262968 Aseprite 11823 80 11903 0.9932790052927833 A Short Hike 11645 87 11732 0.9925843845891579 CULTIC 2021 16 2037 0.9921453117329406 Senren＊Banka 10593 84 10677 0.9921326215228997 Ib 1814 15 1829 0.9917987971569163 planetarian HD 1952 20 1972 0.9898580121703854 Word Game: Episode 0 4205 45 4250 0.9894117647058823 Riddle Joker 2995 33 3028 0.989101717305152 Our Life: Beginnings & Always 7953 90 8043 0.988810145468109 People Playground 142920 1649 144569 0.9885936819096763 Summer Pockets 1811 21 1832 0.9885371179039302 Maitetsu:Last Run!! 2305 27 2332 0.9884219554030875 Epic Battle Fantasy 5 4307 52 4359 0.9880706584078918 Portal 2 305671 3770 309441 0.9878167405094994 Vampire Survivors 130311 1624 131935 0.9876909084018646 The Room 4: Old Sins 10294 130 10424 0.9875287797390637 ATRI -My Dear Moments- 9009 115 9124 0.9873958790004385 The Henry Stickmin Collection 32913 427 33340 0.9871925614877025 Batman: Arkham City 1978 26 2004 0.9870259481037924 ULTRAKILL 40050 548 40598 0.9865017981181339 pureya 1862 26 1888 0.986228813559322 Milo and the Magpies 1790 25 1815 0.9862258953168044 Tiny Bunny 8914 125 9039 0.986171036619095 Hades 199960 2829 202789 0.9860495391761881 Far Away 4405 63 4468 0.9858997314234557 Touhou Tenkuushou ~ Hidden Star in Four Seasons. 4396 64 4460 0.9856502242152466 CLANNAD 6314 92 6406 0.9856384639400562 Cube Escape Collection 3906 58 3964 0.9853683148335015 Grimm's Hollow 10209 152 10361 0.9853296013898273 The Supper 3020 45 3065 0.9853181076672104 Walkabout Mini Golf VR 1770 27 1797 0.9849749582637729 Half-Life: Alyx 73942 1156 75098 0.9846067804735146 Portal 111786 1752 113538 0.9845690429635893 Rhythm Doctor 15908 250 16158 0.9845277880925857 Cats Organized Neatly 2279 36 2315 0.9844492440604752 Sucker for Love: First Date 1736 28 1764 0.9841269841269841 Sabbat of the Witch 1918 31 1949 0.9840944073884043 Sakuya Izayoi Gives You Advice And Dabs 1753 30 1783 0.9831744251261918 Kind Words (lo fi chill beats to write to) 7654 133 7787 0.9829202517015538 The Test: Final Revelation 4569 81 4650 0.9825806451612903 Katana ZERO 49239 875 50114 0.9825398092349443 RimWorld 142201 2550 144751 0.9823835413917693 Will You Snail? 1859 34 1893 0.9820390913893291 OneShot 30623 561 31184 0.9820100051308364 TY the Tasmanian Tiger 2258 42 2300 0.9817391304347826 Stardew Valley 497558 9283 506841 0.9816845914201889 Neon White 6738 126 6864 0.9816433566433567 Baba Is You 16162 310 16472 0.9811801845556095 OMORI 46239 889 47128 0.9811364793753182 Aokana - Four Rhythms Across the Blue 3337 65 3402 0.9808935920047032 Master Of Pottery 2257 44 2301 0.9808778791829639 Wallpaper Engine 561096 11031 572127 0.9807193158162436 Wobbledogs 4880 96 4976 0.9807073954983923 Firework 28285 557 28842 0.9806878857222107 Tales of the Black Forest 7855 155 8010 0.980649188514357 The Test: Hypothesis Rising 5122 102 5224 0.9804747320061256 Bugsnax 1907 38 1945 0.9804627249357326 A Hat in Time 43958 881 44839 0.9803519257788978 SuchArt: Creative Space 5729 115 5844 0.980321697467488 One Finger Death Punch 15628 314 15942 0.980303600552001 There Is No Game: Wrong Dimension 17334 352 17686 0.9800972520637793 Gravitas 5747 119 5866 0.9797136038186157 Monster Prom 2: Monster Camp 4645 97 4742 0.9795444959932518 Helltaker 105952 2213 108165 0.9795405168030324 Hylics 3038 64 3102 0.9793681495809156 Alba: A Wildlife Adventure 3365 71 3436 0.979336437718277 Bug Fables: The Everlasting Sapling 3622 77 3699 0.979183563125169 Chicory: A Colorful Tale 1975 42 2017 0.9791769955379276 Marco & The Galaxy Dragon 4251 91 4342 0.9790419161676647 Kindergarten 2 2896 62 2958 0.9790398918187965 Slay the Spire 116347 2494 118841 0.9790139766578875 Totally Accurate Battle Simulator 93141 1999 95140 0.97898885852428 Virtual Cottage 6870 148 7018 0.9789113707609005 Slime Rancher 97207 2099 99306 0.978863311380984 Finding Paradise 13881 300 14181 0.97884

The best rated game, for games with more ratings than the mean of ratings, is Aventura Copilului Albastru și Urât.

#### Are there years with more releases ? Were there more or fewer game releases during the Covid, for example ?

In [ ]:
date_df = dataset.withColumn('release_date', F.col('data').getField('release_date'))
date_df = date_df.withColumn('year', F.substring('release_date', 0, 4))
date_df = date_df.groupBy('year').count().orderBy('year')
display(date_df)

year count 99 1997 2 1998 1 1999 3 2000 2 2001 4 2002 1 2003 3 2004 6 2005 6 2006 61 2007 98 2008 159 2009 311 2010 288 2011 267 2012 345 2013 471 2014 1557 2015 2576 2016 4185 2017 6017 2018 7678 2019 6968 2020 8305 2021 8823 2022 7455

Databricks visualization. Run in Databricks to view.

In [ ]:
date_df_bis = date_df.orderBy(date_df['count'].desc()).limit(5)
display(date_df_bis)

year count 2021 8823 2020 8305 2018 7678 2022 7455 2019 6968

The year with the more releases is 2021 with 8823 releases, and the second is 2020. So we can say that it seems to be more games seleased during the Covid.

#### How are the prizes distributed ? Are there many games with a discount ?

In [ ]:
price_df = dataset.select('data.price', 'data.discount')
price_df = price_df.withColumn("price", price_df.price.cast("int")).withColumn("discount", price_df.discount.cast("int"))
price_dist_df = price_df.groupBy("price").count().orderBy("price")
display(price_dist_df)

price count 0 7780 28 20 29 11 30 2 31 6 37 19 38 7 39 7 41 10 44 1 45 2 49 303 50 25 51 51 53 5 54 21 56 2 57 3 59 97 61 2 62 1 64 3 65 1 67 2 69 38 71 1 74 34 75 2 76 1 77 4 79 40 80 1 81 2 83 2 84 3 89 25 90 32 91 4 95 1 98 1 99 5243 100 16 103 4 104 6 107 1 109 5 111 1 119 40 123 2 124 21 129 8 132 1 133 2 134 3 135 1 136 1 139 19 140 1 142 1 145 1 147 2 149 73 150 6 154 3 155 1 158 2 159 25 164 1 169 7 174 12 179 23 183 1 187 1 188 1 189 2 191 1 194 2 195 1 197 3 198 1 199 4193 200 8 203 1 209 34 214 1 216 1 219 14 222 1 224 12 229 1 230 1 236 1 239 27 244 4 245 1 249 99 250 5 251 1 254 2 259 11 263 1 269 8 271 4 274 1 279 22 288 1 290 1 293 1 294 1 299 3639 300 9 303 1 309 4 314 1 319 6 324 6 329 2 333 1 339 6 349 45 350 1 359 20 360 1 369 1 373 1 374 29 375 1 377 2 379 2 386 1 388 1 389 8 391 1 397 2 399 2530 400 6 419 11 420 8 424 4 428 1 430 1 433 1 439 4 449 41 454 3 459 1 463 1 464 1 479 18 485 1 488 1 489 3 493 3 494 2 495 1 499 6250 500 20 509 10 510 2 514 1 519 4 524 7 529 1 539 4 549 6 550 1 557 1 558 1 559 9 565 1 569 1 573 1 577 1 579 1 584 2 590 1 594 2 599 1854 600 5 610 1 619 1 623 1 624 5 629 9 631 1 636 1 639 6 649 13 659 2 666 3 669 7 674 4 679 7 680 1 698 1 699 1856 700 1 706 1 714 2 719 5 736 1 749 40 750 1 764 1 769 1 777 1 779 7 795 1 799 1580 800 3 809 1 819 1 824 4 839 5 849 8 854 1 870 1 874 1 879 1 888 1 890 1 898 1 899 753 900 2 909 3 911 1 929 1 949 1 959 3 969 1 974 13 979 3 987 1 989 7 990 6 995 2 998 1 999 6126 1000 10 1004 3 1019 3 1025 1 1039 4 1049 9 1079 4 1099 430 1104 2 1119 1 1124 7 1139 1 1149 1 1169 5 1189 1 1190 1 1199 822 1200 4 1224 1 1240 1 1249 14 1259 5 1274 5 1279 1 1290 1 1295 1 1299 796 1313 1 1329 2 1337 1 1339 1 1349 9 1359 2 1399 276 1438 1 1439 1 1449 2 1450 1 1473 1 1495 1 1499 2878 1500 9 1510 1 1519 2 1529 3 1558 1 1574 1 1599 230 1600 1 1624 4 1639 1 1666 1 1699 185 1724 1 1749 7 1777 1 1799 286 1874 2 1889 1 1899 141 1900 2 1949 2 1969 1 1979 1 1984 1 1990 2 1995 2 1996 1 1997 1 1999 2820 2000 5 2004 1 2024 1 2099 5 2109 1 2124 1 2199 9 2249 4 2260 1 2279 1 2299 5 2339 1 2397 1 2399 9 2449 1 2459 1 2479 1 2499 862 2500 3 2599 2 2699 6 2799 2 2899 2 2990 1 2995 1 2998 2 2999 865 3000 1 3196 1 3199 3 3299 1 3366 1 3499 155 3500 1 3595 1 3599 4 3749 1 3900 1 3939 1 3990 1 3999 428 4000 1 4495 1 4498 1 4499 44 4500 1 4969 1 4999 190 5274 1 5499 15 5624 1 5795 1 5995 1 5999 187 6495 1 6499 6 6903 1 6995 1 6999 25 7499 3 7999 13 8499 1 8999 5 9499 4 9900 1 9999 24 11999 2 12499 1 12999 5 14900 1 14999 6 15999 1 19999 17 24900 1 26999 1 29990 1 99900 1

Databricks visualization. Run in Databricks to view.

In [ ]:
no_discount_games = price_df.filter(price_df.discount == 0).count()
discount_games = price_df.filter(price_df.discount > 0).count()
print('No dicount games :', no_discount_games)
print('Dicount games :', discount_games)
print('More no dicount than dicount ?', (no_discount_games > discount_games))

No dicount games : 53173
Dicount games : 2518
More no dicount than dicount ? True


We can see the price distribution with the visualisation. A lot of the games are free, the biggest part is under 500$, but the max value for only one game can reach 99 900$, followed by another game which cost is 29 990$.\
There are much more games without a discount (53173) than with (2518).

#### What are the most represented languages ?

In [ ]:
dataset.groupBy("data.languages").count().orderBy(col("count").desc()).show()

+--------------------+-----+
|           languages|count|
+--------------------+-----+
|             English|29163|
|    English, Russian| 1881|
|English, Simplifi...| 1200|
|   English, Japanese| 1015|
|English, Not supp...|  683|
|     English, German|  605|
|     English, French|  510|
|English, French, ...|  493|
|English, Portugue...|  463|
|English, Simplifi...|  326|
|  Simplified Chinese|  318|
|English, Spanish ...|  300|
|English, French, ...|  268|
|English, French, ...|  255|
|English, Japanese...|  208|
|English, Japanese...|  208|
|     English, Korean|  206|
|English, French, ...|  202|
|English, French, ...|  194|
|English, French, ...|  178|
+--------------------+-----+
only showing top 20 rows



In [ ]:
languages_df = dataset.withColumn('language_list', split(dataset['data.languages'], ', '))
languages_df = languages_df.withColumn('language', explode(languages_df['language_list']))
languages_df = languages_df.groupBy('language').count()
languages_df = languages_df.orderBy(languages_df['count'].desc())
display(languages_df)

language count English 55116 German 14019 French 13426 Russian 12922 Simplified Chinese 12782 Spanish - Spain 12233 Japanese 10368 Italian 9304 Portuguese - Brazil 6750 Korean 6599 Traditional Chinese 6307 Polish 5375 Portuguese - Portugal 4011 Turkish 3602 Dutch 3080 Spanish - Latin America 2732 Czech 2352 Swedish 2047 Ukrainian 1928 Hungarian 1922 Arabic 1796 Danish 1717 Thai 1699 Finnish 1614 Norwegian 1613 Greek 1444 Romanian 1431 Not supported 1276 Bulgarian 1256 Vietnamese 1133 Indonesian 54 Slovak 47 Catalan 38 Hindi 26 Hebrew 25 Belarusian 23 Serbian 20 Basque 17 Malay 14 Persian 12 Croatian 12 Lithuanian 12 Latvian 12 Portuguese 11 11 Estonian 10 Filipino 7 Slovenian 6 Welsh 6 Galician 6 Icelandic 5 Irish 5 Georgian 4 English[b]*[/b] 4 Afrikaans 4 Albanian 4 Bangla 3 Urdu 3 Bosnian 3 Tamil 3 Kazakh 3 German[b]*[/b] 2 Telugu 2 Luxembourgish 2 #lang_slovakian 2 German; 2 Swahili 2 Azerbaijani 2 Korean 1 Kannada 1 Russian
[b]*[/b] 1 French[b]*[/b] 1 Japanese 

[b]*[/b] 1 English (full audio) 1 English Dutch English 1 Mongolian 1 Hungarian,Polish 1 Maori 1 Spanish - Spain
[b]*[/b] 1 Italian 

[b]*[/b] 1 Valencian 1 Dari 1 Marathi 1 Korean[b]*[/b] 1 Spanish - Spain[b]*[/b] 1 English
Russian
Spanish - Spain
Japanese
Czech 1 Traditional Chinese (text only) 1 Macedonian 1 Punjabi (Gurmukhi) 1 Uzbek 1 Italian[b]*[/b] 1 Russian
English
Spanish - Spain
French
Japanese
Czech 1 (all with full audio support) 1

More represented languages are English first and from far away, and then German and French.

#### Are there many games prohibited for children under 16/18 ?

In [ ]:
age_16 = dataset.filter(dataset.data.required_age == "16").count()
age_18 = dataset.filter(dataset.data.required_age == "18").count()
print("The number of games prohibited for children under 16/18 is :", (age_16 + age_18))

The number of games prohibited for children under 16/18 is : 261


### Genres analysis

#### What are the most represented genres ?

In [ ]:
genre_df = dataset.withColumn('genre_list', split(dataset['data.genre'], ', '))
genre_df = genre_df.withColumn('genre', explode(genre_df['genre_list']))
genre_df = genre_df.groupBy('genre').count()
genre_df = genre_df.orderBy(genre_df['count'].desc())
display(genre_df)

genre count Indie 39681 Action 23759 Casual 22086 Adventure 21431 Strategy 10895 Simulation 10836 RPG 9534 Early Access 6145 Free to Play 3393 Sports 2666 Racing 2155 Massively Multiplayer 1460 Utilities 682 Design & Illustration 406 Animation & Modeling 322 Education 317 Video Production 247 Audio Production 195 Violent 168 Software Training 164 161 Game Development 159 Photo Editing 105 Gore 99 Web Publishing 89 Sexual Content 54 Nudity 45 Accounting 16 Movie 1

The most represented genres are first Indie, second Action, and third Casual.

#### Are there any genres that have a better positive/negative review ratio ?

In [ ]:
genre_ratio_df = dataset.select('data.genre', 'data.positive', 'data.negative')
genre_ratio_df = genre_ratio_df.withColumn('genre_list', split(genre_ratio_df['genre'], ', '))
genre_ratio_df = genre_ratio_df.withColumn('len_genre_list', size(col('genre_list')))
genre_ratio_df = genre_ratio_df.withColumn('pos', (col('positive')/col('len_genre_list'))).drop('positive')
genre_ratio_df = genre_ratio_df.withColumn('neg', (col('negative')/col('len_genre_list'))).drop('negative').drop('len_genre_list')
genre_ratio_df = genre_ratio_df.withColumn('genre', explode(genre_ratio_df['genre_list'])).drop('genre_list')
genre_ratio_df = genre_ratio_df.select('*').groupBy('genre').sum()
genre_ratio_df = genre_ratio_df.withColumn('positive',col('sum(pos)')).drop(col('sum(pos)'))
genre_ratio_df = genre_ratio_df.withColumn('negative',col('sum(neg)')).drop(col('sum(neg)'))
display(genre_ratio_df)

genre positive negative Education 4761.7036130536135 1259.5752997002996 Massively Multiplayer 1861497.8686147206 698415.3407287162 Sexual Content 1385.1833333333334 341.0492063492064 Adventure 1.0430175838059181E7 1811069.062554102 Sports 919666.34520202 254530.6879509382 Accounting 70.21194638694638 35.61934731934732 Audio Production 28406.048851148844 3830.1129981129966 Video Production 42348.59051781553 6801.403871128871 Animation & Modeling 140696.2845654346 7025.625696525699 Racing 882636.1325036077 149109.00541125538 Gore 6538.833333333332 1372.9408730158725 Design & Illustration 131377.63694638698 7236.569347319351 Software Training 4222.7631368631355 1093.2395854145855 Web Publishing 10154.038136863133 1457.2038711288715 Photo Editing 97234.40004162505 2434.964585414584 Utilities 201133.64329559336 21794.89434731936 Violent 9972.161904761912 2708.844444444446 Game Development 9341.89015151515 777.4567099567098 Movie 206.25 188.0 Nudity 1650.7178571428572 569.7761904761905 Early Access 1074019.0535714282 214599.053571429 Casual 3238459.393981025 478609.7732073477 189649.0 27744.0 Action 2.6080641174170278E7 4154668.756998589 Strategy 5560114.645995677 929726.85660173 Indie 1.072395685667944E7 1283958.5426517797 Free to Play 6899702.290806417 1390285.511302585 RPG 7974956.769805211 1226183.3050144278 Simulation 5389557.272979795 790355.8276334786

In [ ]:
genre_ratio_df = genre_ratio_df.select('*', (genre_ratio_df.positive / genre_ratio_df.negative).alias('genre_ratio'))
genre_ratio_df = genre_ratio_df.orderBy(genre_ratio_df['genre_ratio'].desc())
display(genre_ratio_df)

genre positive negative genre_ratio Photo Editing 97234.40004162505 2434.964585414584 39.932572581982605 Animation & Modeling 140696.2845654346 7025.625696525699 20.02615719123942 Design & Illustration 131377.63694638698 7236.569347319351 18.154684995183985 Game Development 9341.89015151515 777.4567099567098 12.015961830254605 Utilities 201133.64329559336 21794.89434731936 9.228475260781963 Indie 1.072395685667944E7 1283958.5426517797 8.35226099631775 Audio Production 28406.048851148844 3830.1129981129966 7.416504125372754 Web Publishing 10154.038136863133 1457.2038711288715 6.968165771476417 189649.0 27744.0 6.835676182237601 Simulation 5389557.272979795 790355.8276334786 6.819152949270288 Casual 3238459.393981025 478609.7732073477 6.766387932864108 RPG 7974956.769805211 1226183.3050144278 6.503886276376414 Action 2.6080641174170278E7 4154668.756998589 6.277429730164921 Video Production 42348.59051781553 6801.403871128871 6.226448439208283 Strategy 5560114.645995677 929726.85660173 5.980374350288862 Racing 882636.1325036077 149109.00541125538 5.919401917202934 Adventure 1.0430175838059181E7 1811069.062554102 5.759126503629732 Early Access 1074019.0535714282 214599.053571429 5.004770690724143 Free to Play 6899702.290806417 1390285.511302585 4.962795220632023 Gore 6538.833333333332 1372.9408730158725 4.762647439412154 Sexual Content 1385.1833333333334 341.0492063492064 4.061535132015582 Software Training 4222.7631368631355 1093.2395854145855 3.862614556956197 Education 4761.7036130536135 1259.5752997002996 3.7804040887326087 Violent 9972.161904761912 2708.844444444446 3.6813342771356856 Sports 919666.34520202 254530.6879509382 3.6131845342723046 Nudity 1650.7178571428572 569.7761904761905 2.8971337952245237 Massively Multiplayer 1861497.8686147206 698415.3407287162 2.665316409963821 Accounting 70.21194638694638 35.61934731934732 1.9711744226377061 Movie 206.25 188.0 1.0970744680851063

In [ ]:
positive_ratio = genre_ratio_df.filter(genre_ratio_df.genre_ratio > 1).count()
negative_ratio = genre_ratio_df.filter(genre_ratio_df.genre_ratio < 1).count()
print(f"There are {positive_ratio} genres with a positive ratio, and {negative_ratio} genres with a negative ratio.")

There are 29 genres with a positive ratio, and 0 genres with a negative ratio.


The genre with the best positive ratio is Photo Editing. There are no genre with negative ratio.

#### Do some publishers have favorite genres ?

In [ ]:
fav_genre_df = dataset.select('data.genre', 'data.publisher')
fav_genre_df = fav_genre_df.withColumn('genre_list', split(fav_genre_df['genre'], ', '))
#fav_genre_df = fav_genre_df.withColumn('len_genre_list', size(col('genre_list')))
#fav_genre_df = fav_genre_df.withColumn('count_with_size', 1/col('len_genre_list'))).drop('len_genre_list')
fav_genre_df = fav_genre_df.withColumn('genre', explode(fav_genre_df['genre_list'])).drop('genre_list')
fav_genre_df = fav_genre_df.groupBy('publisher', 'genre').count()
fav_genre_df = fav_genre_df.orderBy(fav_genre_df['publisher'])
fav_genre_df = fav_genre_df.filter((fav_genre_df["publisher"] != "") & (fav_genre_df["publisher"] != " ") & (fav_genre_df["genre"] != ""))
display(fav_genre_df)

publisher genre count AK Studio Adventure 1 AK Studio Action 1 AK Studio Casual 1 AK Studio Indie 2 AK Studio Racing 1 ARVORE Immersive Experiences Strategy 1 ARVORE Immersive Experiences Adventure 1 ARVORE Immersive Experiences Casual 1 ARVORE Immersive Experiences Action 1 ARVORE Immersive Experiences Indie 1 Alon Zubina Indie 1 Alon Zubina Simulation 1 Alon Zubina Adventure 1 Appnori Inc. Early Access 1 Appnori Inc. Sports 1 Art Games Studio S.A. Casual 1 Art Games Studio S.A. Indie 1 Asterion Games Adventure 1 Asterion Games Indie 1 Asterion Games Strategy 1 Asterion Games RPG 1 Attack Studio Adventure 1 Attack Studio Casual 1 Aurora software Indie 1 Aurora software Action 1 BBB Games Indie 1 BBB Games Casual 1 BBB Games Action 1 BD Games Indie 1 BD Games Strategy 1 BD Games RPG 1 BD Games Adventure 1 Beach Day Studios Indie 1 Beach Day Studios Early Access 1 Beach Day Studios Action 1 Beach Day Studios Racing 1 Bear in the Night Indie 1 Bear in the Night Adventure 1 Bear in the Night Casual 1 Big Fish Games Adventure 1 Big Fish Games Casual 1 Boogygames Studios Adventure 1 Boogygames Studios Indie 1 Boogygames Studios Simulation 1 Boogygames Studios Casual 1 Boogygames Studios Sports 1 CGevo Adventure 1 CGevo Action 1 CGevo Indie 1 Chongqing Juxin Technology Co., Ltd Indie 1 Chongqing Juxin Technology Co., Ltd Action 1 Chongqing Juxin Technology Co., Ltd Casual 1 Chongqing Juxin Technology Co., Ltd Massively Multiplayer 1 Cotton Game Strategy 1 Cotton Game Casual 1 Cotton Game Adventure 1 Cotton Game Indie 1 Dipl. Ing. Rolf-Dieter Klein Simulation 1 Dipl. Ing. Rolf-Dieter Klein Strategy 1 Dipl. Ing. Rolf-Dieter Klein Adventure 1 Droid Riot Action 1 EXTREMESOFT BILISIM REKLAMCILIK TICARET LIMITED SIRKETI Simulation 1 EXTREMESOFT BILISIM REKLAMCILIK TICARET LIMITED SIRKETI Early Access 1 EXTREMESOFT BILISIM REKLAMCILIK TICARET LIMITED SIRKETI Action 1 EXTREMESOFT BILISIM REKLAMCILIK TICARET LIMITED SIRKETI Adventure 1 EXTREMESOFT BILISIM REKLAMCILIK TICARET LIMITED SIRKETI Indie 1 EastFog Studios Indie 1 EastFog Studios Strategy 1 EastFog Studios RPG 1 EastFog Studios Adventure 1 EastFog Studios Action 1 EastFog Studios Early Access 1 EastFog Studios Simulation 1 Flyhigh Works Casual 2 Flyhigh Works Action 2 FurGoldGames Action 1 FurGoldGames Adventure 1 GAMELAB Action 1 GAMELAB Casual 1 GAMELAB Indie 1 Game for people Action 1 Game for people Sports 1 Game for people Indie 1 Game for people Casual 1 Genuine Studio Ltd Adventure 1 Genuine Studio Ltd Indie 1 Genuine Studio Ltd Casual 1 Golden Dragon Studio Casual 1 GrabTheGames Indie 1 GrabTheGames Adventure 1 Green Sauce Games Casual 1 Green Sauce Games Indie 1 Green Sauce Games Adventure 1 H2 Interactive Co., Ltd. Adventure 1 H2 Interactive Co., Ltd. Action 1 H2 Interactive Co., Ltd. RPG 1 Hangover Cat Purrroduction Casual 2 Hangover Cat Purrroduction Indie 2 HongbinGame Casual 1 HongbinGame RPG 1 Iful GS Indie 1 Iful GS Simulation 1 Iful GS Casual 1 Immersion Adventure 1 Immersion Sports 1 Immersion Simulation 1 Immersion Indie 1 Immersion Casual 1 Indevelopment Productions Early Access 1 Indevelopment Productions Action 1 Indevelopment Productions Indie 1 Indevelopment Productions Casual 1 Inertia Game Studios Casual 1 Inertia Game Studios Indie 1 Inertia Game Studios Action 1 JanduSoft Adventure 1 JanduSoft Casual 1 JanduSoft Action 1 JanduSoft Indie 1 Jetdogs Studios Adventure 2 Jetdogs Studios Casual 2 Jetdogs Studios Action 1 Jetdogs Studios Strategy 2 JoyBits Ltd. Action 1 JoyBits Ltd. Indie 1 Kokutou Umeboshi RPG 1 Kokutou Umeboshi Simulation 1 MV Games Adventure 1 MV Games Casual 1 MV Games Indie 1 Maciej Targoni Indie 1 Madmind Studio Action 1 Madmind Studio Indie 1 Metal Fox Indie 1 NGELGAMES Strategy 1 NGELGAMES Action 1 NGELGAMES Simulation 1 Night Steed Games Adventure 1 Night Steed Games Indie 1 Night Steed Games Action 1 OnBlind Adventure 1 OnBlind Indie 1 OnBlind Action 1 PQube Adventure 1 PQube Casual 1 PQube RPG 1 PQube Action 1 Paper Bunker s.r.o. Racin

In [ ]:
fav_genre_df = fav_genre_df.withColumn('publisher_count', F.sum('count').over(Window.partitionBy('publisher')))
fav_genre_df = fav_genre_df.withColumn('genre_per_publisher_%', (100 * col('count') / col('publisher_count')))
fav_genre_df = fav_genre_df.orderBy(fav_genre_df['publisher_count'].desc(), fav_genre_df['publisher'], fav_genre_df['genre_per_publisher_%'].desc())
display(fav_genre_df)

publisher genre count publisher_count genre_per_publisher_% Big Fish Games Casual 418 833 50.18007202881152 Big Fish Games Adventure 392 833 47.05882352941177 Big Fish Games Simulation 7 833 0.8403361344537815 Big Fish Games Indie 7 833 0.8403361344537815 Big Fish Games Strategy 6 833 0.7202881152460985 Big Fish Games Sports 2 833 0.24009603841536614 Big Fish Games Action 1 833 0.12004801920768307 Choice of Games RPG 139 428 32.47663551401869 Choice of Games Indie 136 428 31.77570093457944 Choice of Games Adventure 112 428 26.16822429906542 Choice of Games Casual 28 428 6.542056074766355 Choice of Games Action 13 428 3.0373831775700935 Boogygames Studios Indie 78 395 19.746835443037973 Boogygames Studios Casual 76 395 19.240506329113924 Boogygames Studios Strategy 71 395 17.974683544303797 Boogygames Studios Adventure 67 395 16.962025316455698 Boogygames Studios Simulation 42 395 10.632911392405063 Boogygames Studios Sports 22 395 5.569620253164557 Boogygames Studios RPG 18 395 4.556962025316456 Boogygames Studios Action 15 395 3.7974683544303796 Boogygames Studios Racing 4 395 1.0126582278481013 Boogygames Studios Free to Play 1 395 0.25316455696202533 Boogygames Studios Early Access 1 395 0.25316455696202533 HH-Games Casual 132 340 38.8235294117647 HH-Games Indie 69 340 20.294117647058822 HH-Games Strategy 48 340 14.117647058823529 HH-Games Adventure 39 340 11.470588235294118 HH-Games Action 38 340 11.176470588235293 HH-Games Simulation 12 340 3.5294117647058822 HH-Games Sports 1 340 0.29411764705882354 HH-Games RPG 1 340 0.29411764705882354 Sekai Project Casual 99 326 30.368098159509202 Sekai Project Indie 88 326 26.993865030674847 Sekai Project Adventure 51 326 15.644171779141104 Sekai Project Simulation 24 326 7.361963190184049 Sekai Project Action 21 326 6.441717791411043 Sekai Project RPG 16 326 4.9079754601226995 Sekai Project Strategy 8 326 2.4539877300613497 Sekai Project Free to Play 6 326 1.8404907975460123 Sekai Project Early Access 5 326 1.5337423312883436 Sekai Project Sexual Content 4 326 1.2269938650306749 Sekai Project Nudity 2 326 0.6134969325153374 Sekai Project Violent 1 326 0.3067484662576687 Sekai Project Sports 1 326 0.3067484662576687 Alawar Entertainment Casual 105 322 32.608695652173914 Alawar Entertainment Adventure 95 322 29.503105590062113 Alawar Entertainment Indie 76 322 23.60248447204969 Alawar Entertainment Strategy 39 322 12.111801242236025 Alawar Entertainment Simulation 4 322 1.2422360248447204 Alawar Entertainment RPG 1 322 0.3105590062111801 Alawar Entertainment Action 1 322 0.3105590062111801 Alawar Entertainment Sports 1 322 0.3105590062111801 Hede Action 54 310 17.419354838709676 Hede Indie 54 310 17.419354838709676 Hede Simulation 45 310 14.516129032258064 Hede Casual 40 310 12.903225806451612 Hede Adventure 36 310 11.612903225806452 Hede Strategy 32 310 10.32258064516129 Hede Sports 13 310 4.193548387096774 Hede RPG 12 310 3.870967741935484 Hede Early Access 12 310 3.870967741935484 Hede Racing 8 310 2.5806451612903225 Hede Massively Multiplayer 2 310 0.6451612903225806 Hede Free to Play 2 310 0.6451612903225806 Piece Of Voxel Indie 79 300 26.333333333333332 Piece Of Voxel Casual 62 300 20.666666666666668 Piece Of Voxel Strategy 41 300 13.666666666666666 Piece Of Voxel Simulation 41 300 13.666666666666666 Piece Of Voxel Adventure 33 300 11.0 Piece Of Voxel Action 30 300 10.0 Piece Of Voxel Racing 7 300 2.3333333333333335 Piece Of Voxel RPG 3 300 1.0 Piece Of Voxel Massively Multiplayer 2 300 0.6666666666666666 Piece Of Voxel Early Access 1 300 0.3333333333333333 Piece Of Voxel Sports 1 300 0.3333333333333333 Laush Studio Indie 124 276 44.927536231884055 Laush Studio Casual 87 276 31.52173913043478 Laush Studio Action 20 276 7.246376811594203 Laush Studio Simulation 18 276 6.521739130434782 Laush Studio Adventure 14 276 5.072463768115942 Laush Studio Racing 5 276 1.8115942028985508 Laush Studio Sports 4 276 1.4492753623188406 Laush Studio Strategy 3 276 1.0869565217391304 Laush Studio

In [ ]:
publisher_1 = fav_genre_df.filter(fav_genre_df["publisher"] == "Big Fish Games")
display(publisher_1)

publisher genre count publisher_count genre_per_publisher_% Big Fish Games Casual 418 833 50.18007202881152 Big Fish Games Adventure 392 833 47.05882352941177 Big Fish Games Simulation 7 833 0.8403361344537815 Big Fish Games Indie 7 833 0.8403361344537815 Big Fish Games Strategy 6 833 0.7202881152460985 Big Fish Games Sports 2 833 0.24009603841536614 Big Fish Games Action 1 833 0.12004801920768307

Databricks visualization. Run in Databricks to view.

In [ ]:
publisher_2 = fav_genre_df.filter(fav_genre_df["publisher"] == "Choice of Games")
display(publisher_2)

publisher genre count publisher_count genre_per_publisher_% Choice of Games RPG 139 428 32.47663551401869 Choice of Games Indie 136 428 31.77570093457944 Choice of Games Adventure 112 428 26.16822429906542 Choice of Games Casual 28 428 6.542056074766355 Choice of Games Action 13 428 3.0373831775700935

Databricks visualization. Run in Databricks to view.

In [ ]:
publisher_3 = fav_genre_df.filter(fav_genre_df["publisher"] == "Boogygames Studios")
display(publisher_3)

publisher genre count publisher_count genre_per_publisher_% Boogygames Studios Indie 78 395 19.746835443037973 Boogygames Studios Casual 76 395 19.240506329113924 Boogygames Studios Strategy 71 395 17.974683544303797 Boogygames Studios Adventure 67 395 16.962025316455698 Boogygames Studios Simulation 42 395 10.632911392405063 Boogygames Studios Sports 22 395 5.569620253164557 Boogygames Studios RPG 18 395 4.556962025316456 Boogygames Studios Action 15 395 3.7974683544303796 Boogygames Studios Racing 4 395 1.0126582278481013 Boogygames Studios Free to Play 1 395 0.25316455696202533 Boogygames Studios Early Access 1 395 0.25316455696202533

Databricks visualization. Run in Databricks to view.

As we can see for the first three publisher, it seems that some have favorite genres, when others are more balanced. \
It is obvious for Big Fish Games who is clearly specialized in Casual and Adventure games genres (more than 97% of their games of those 2 genres). For Choice of Games we can see a preference for RPG, Indie and Adventure games genres (more than 90% of their games of those 3 genres). \
But for the publisher Boogygames Studios, genres are much more balanced for games publications, they have 5 main genres between 17% and 20% of their games publications, but they still have 4 other genres with significative percentage.

#### What are the most lucrative genres ?

In [ ]:
lucrative_df = dataset.select('data.genre', 'data.price')
lucrative_df = lucrative_df.withColumn('genre_list', split(lucrative_df['genre'], ', '))
lucrative_df = lucrative_df.withColumn('genre', explode(lucrative_df['genre_list'])).drop('genre_list')
lucrative_df = lucrative_df.withColumn("price", lucrative_df.price.cast("int"))
lucrative_df = lucrative_df.select('*').groupBy('genre').sum()
lucrative_df = lucrative_df.orderBy(lucrative_df['sum(price)'].desc())
display(lucrative_df)

genre sum(price) Indie 26063036 Action 18358769 Adventure 17158179 Casual 12383583 Simulation 9851654 Strategy 9157201 RPG 8621295 Early Access 5375795 Sports 2385529 Racing 1771645 Utilities 780919 Design & Illustration 773770 Massively Multiplayer 730035 Animation & Modeling 604597 Video Production 468285 Education 454632 Audio Production 383077 Game Development 338387 Software Training 312136 Photo Editing 213425 Web Publishing 193987 Free to Play 97233 Violent 88697 62618 Gore 56436 Sexual Content 37126 Nudity 31315 Accounting 23092 Movie 0

The most lucrative genres are first Indie games with 26 063 036$, second Action games with 18 358 769$, third Adventure games with 17 158 179$.

### Platform analysis

#### Are most games available on Windows/Mac/Linux instead ?

In [ ]:
platform_df = dataset.select('data.platforms.linux', 'data.platforms.mac', 'data.platforms.windows')
platform_df = platform_df.withColumn("linux", platform_df.linux.cast("int")).withColumn("mac", platform_df.mac.cast("int"))\
    .withColumn("windows", platform_df.windows.cast("int"))
platform_df = platform_df.select(sum(platform_df.linux).alias('linux_sum'), sum(platform_df.mac).alias('mac_sum'),\
    sum(platform_df.windows).alias('windows_sum'))
display(platform_df)

linux_sum mac_sum windows_sum 8458 12770 55676

There are much more games available on Windows than Mac or Linux. Windows comes in first with 55 676 games availabe on its platform, then Mac is second with 12 770 games availabe, and Linux is the last with 8 458 games availabe.

#### Do certain genres tend to be preferentially available on certain platforms ?

In [ ]:
platform_genre_df = dataset.select('data.genre', 'data.platforms.linux', 'data.platforms.mac', 'data.platforms.windows')
platform_genre_df = platform_genre_df.withColumn("linux", platform_genre_df.linux.cast("int")).withColumn("mac", platform_genre_df.mac.cast("int"))\
    .withColumn("windows", platform_genre_df.windows.cast("int"))
platform_genre_df = platform_genre_df.withColumn('genre_list', split(platform_genre_df['genre'], ', '))
platform_genre_df = platform_genre_df.withColumn('genre', explode(platform_genre_df['genre_list'])).drop('genre_list')
platform_genre_df = platform_genre_df.select('*').groupBy('genre').sum()
platform_genre_df = platform_genre_df.withColumn('total_per_genre', (col('sum(linux)') + col('sum(mac)') + col('sum(windows)')))
platform_genre_df = platform_genre_df.orderBy(platform_genre_df['total_per_genre'].desc())
display(platform_genre_df)

genre sum(linux) sum(mac) sum(windows) total_per_genre Indie 6978 9935 39676 56589 Action 3379 4564 23755 31698 Casual 3305 5130 22082 30517 Adventure 3302 5039 21427 29768 Strategy 1826 3005 10892 15723 Simulation 1532 2439 10832 14803 RPG 1524 2248 9533 13305 Early Access 632 900 6145 7677 Free to Play 474 845 3391 4710 Sports 287 506 2665 3458 Racing 304 424 2154 2882 Massively Multiplayer 164 270 1459 1893 Utilities 49 102 681 832 Design & Illustration 54 100 405 559 Animation & Modeling 38 74 322 434 Education 19 56 317 392 Video Production 6 29 247 282 42 55 159 256 Game Development 35 52 159 246 Audio Production 7 41 193 241 Violent 22 33 168 223 Software Training 12 27 164 203 Gore 14 20 99 133 Photo Editing 4 16 105 125 Web Publishing 8 20 89 117 Sexual Content 7 13 54 74 Nudity 7 10 45 62 Accounting 0 4 16 20 Movie 0 0 1 1

For all genres, the availability on platforms are almost the same. Games available on Windows, and then comes Mac and Linux. There is no a preferential platform for a genre of games.

### Ubisoft Analysis

In [ ]:
publisher_df = publisher_df.filter((publisher_df["publisher"] != "") & (publisher_df["publisher"] != " "))
w = Window.orderBy(publisher_df["count"].desc())
publisher_df = publisher_df.withColumn("col_rank", F.rank().over(w))
publisher_df.createOrReplaceTempView('publisher_table')
ubisoft_table_publisher = spark.sql("SELECT * FROM publisher_table WHERE publisher LIKE 'Ubi%' ")
display(ubisoft_table_publisher)

publisher count col_rank Ubisoft 127 9 Ubisoft Entertainment 5 1004 Ubisoft Entertainment 1 6782 Ubisoft - San Francisco 1 6782 Ubisoft® 1 6782

Ubiisoft is the ninth biggest game publisher with 127 games published.

In [ ]:
rate_df2 = dataset.select('data.publisher', 'data.name', 'data.positive', 'data.negative')
rate_df2 = rate_df2.select('*', (rate_df2.positive + rate_df2.negative).alias('total_ratings'))
rate_df2 = rate_df2.select('*', (rate_df2.positive / rate_df2.total_ratings).alias('positive_ratings'))
rate_df2 = rate_df2.orderBy(rate_df2['positive_ratings'].desc())
rate_df2.createOrReplaceTempView('rate_table')
ubisoft_table_ratings = spark.sql("SELECT * FROM rate_table WHERE publisher LIKE 'Ubi%' ")
display(ubisoft_table_ratings)

publisher name positive negative total_ratings positive_ratings Ubisoft South Park: The Stick of Truth 50149 1246 51395 0.975756396536628 Ubisoft Valiant Hearts: The Great War / Soldats Inconnus : Mémoires de la Grande Guerre 20996 954 21950 0.9565375854214123 Ubisoft Trackmania United Forever 1932 109 2041 0.9465948064674179 Ubisoft Tom Clancy's Ghost Recon Desert Siege 86 5 91 0.945054945054945 Ubisoft Rayman Origins 3032 192 3224 0.9404466501240695 Ubisoft Tom Clancy's Splinter Cell Chaos Theory 3454 239 3693 0.9352829677768751 Ubisoft Heroes of Might & Magic V: Tribes of the East 2078 155 2233 0.9305866547245858 Ubisoft Tom Clancy's Ghost Recon 1023 78 1101 0.9291553133514986 Ubisoft Voodoo Dice 13 1 14 0.9285714285714286 Ubisoft Child of Light 11545 928 12473 0.9255992944760683 Ubisoft Dark Messiah of Might & Magic 7795 701 8496 0.9174905838041432 Ubisoft Tom Clancy's Rainbow Six 3 Gold 1376 124 1500 0.9173333333333333 Ubisoft Grow Home 4614 424 5038 0.9158396188963874 Ubisoft Rocksmith 1164 109 1273 0.9143754909662215 Ubisoft Grow Up 1404 133 1537 0.9134677944046844 Ubisoft Cloudberry Kingdom 194 19 213 0.9107981220657277 Ubisoft Rayman Legends 5539 552 6091 0.909374486947956 Ubisoft Driver Parallel Lines 790 82 872 0.9059633027522935 Ubisoft Rocksmith 2014 Edition - Remastered 18369 1921 20290 0.9053228191227205 Ubisoft Brothers in Arms: Hell's Highway 1477 155 1632 0.9050245098039216 Ubisoft Far Cry 3 77934 8629 86563 0.9003153772396982 Ubisoft Dawn of Discovery 369 41 410 0.9 Ubisoft Assassin’s Creed IV Black Flag 48077 5548 53625 0.8965407925407926 Ubisoft Assassin's Creed Odyssey 115326 13969 129295 0.891960245949186 Ubisoft TrackMania Nations Forever 17977 2181 20158 0.8918047425339816 Ubisoft Assassin's Creed 2 34859 4266 39125 0.890964856230032 Ubisoft Assassin’s Creed Brotherhood 14449 1814 16263 0.8884584639980323 Ubisoft TrackMania² Stadium 5524 705 6229 0.8868197142398458 Ubisoft Far Cry 3 - Blood Dragon 13028 1671 14699 0.8863187971970883 Ubisoft Heroes of Might & Magic V 2641 360 3001 0.8800399866711096 Ubisoft Brothers in Arms: Road to Hill 30 1186 164 1350 0.8785185185185185 Ubisoft Brothers in Arms: Earned in Blood 613 87 700 0.8757142857142857 Ubisoft Silent Hunter III 1669 242 1911 0.8733647305075877 Ubisoft Tom Clancy's Splinter Cell 2006 292 2298 0.8729329852045257 Ubisoft Beyond Good and Evil 2572 387 2959 0.8692125718148023 Ubisoft Tom Clancy's Ghost Recon Island Thunder 86 13 99 0.8686868686868687 Ubisoft Tom Clancy's Rainbow Six Siege 942910 143247 1086157 0.8681157512219688 Ubisoft Assassin's Creed Origins 71930 11097 83027 0.8663446830549099 Ubisoft Prince of Persia: The Sands of Time 2361 386 2747 0.8594830724426648 Ubisoft Heroes of Might & Magic V: Hammers of Fate 214 35 249 0.8594377510040161 Ubisoft Assassin's Creed Revelations 11070 1850 12920 0.8568111455108359 Ubisoft ShootMania Storm 698 118 816 0.8553921568627451 Ubisoft The Settlers : Heritage of Kings - History Edition 433 75 508 0.8523622047244095 Ubisoft Might & Magic: Clash of Heroes 1955 339 2294 0.8522231909328684 Ubisoft Tom Clancy's Rainbow Six Vegas 2 3983 701 4684 0.8503415883859948 Ubisoft Prince of Persia: Warrior Within 1894 337 2231 0.8489466606902735 Ubisoft Assassin’s Creed Rogue 10706 1920 12626 0.8479328370030097 Ubisoft Discovery Tour by Assassin’s Creed: Ancient Egypt 115 21 136 0.8455882352941176 Ubisoft Far Cry Primal 21170 3959 25129 0.8424529428150742 Ubisoft Cold Fear 686 130 816 0.8406862745098039 Ubisoft Brawlhalla 254203 48663 302866 0.8393249820052432 Ubisoft Assassin's Creed: Director's Cut Edition 12145 2350 14495 0.83787512935495 Ubisoft Rayman Raving Rabbids 775 151 926 0.8369330453563715 Ubisoft Anno 1800 3684 739 4423 0.8329188333710151 Ubisoft Watch_Dogs 2 48915 9946 58861 0.8310256366694415 Ubisoft Far Cry 4 35946 7350 43296 0.8302383592017738 Ubisoft Tom Clancy’s Splinter Cell Blacklist 13989 2862 16851 0.8301584475698771 Ubisoft Steep 18906 3905 22811 0.8288106615229495 Ubisoft Far Cry 5845 1251

The best rated game from Ubisoft is South Park: The Stick of Truth. It's quite surprising to not see one game of the Assassin's Creed series in their top ten rated games when we know that it's their best sales.

In [ ]:
date_df2 = dataset.select('data.publisher', 'data.release_date')
date_df2 = date_df2.withColumn('year', F.substring('release_date', 0, 4)).drop('release_date')
date_df2.createOrReplaceTempView('date_table')
ubisoft_table_date = spark.sql("SELECT year, COUNT(year) FROM date_table WHERE publisher IN ('Ubisoft') GROUP BY year ORDER BY year")
display(ubisoft_table_date)

year count(year) 1 2006 1 2008 23 2009 12 2010 7 2011 7 2012 6 2013 11 2014 11 2015 10 2016 13 2017 9 2018 5 2019 8 2020 3

The year Ubisoft released the more games is 2008 with 23 games.

In [ ]:
age_16_bis = dataset.filter((dataset.data.required_age == "16") & (dataset.data.publisher == 'Ubisoft')).count()
age_18_bis = dataset.filter((dataset.data.required_age == "18") & (dataset.data.publisher == 'Ubisoft')).count()
print("The number of games prohibited for children under 16/18 from Ubisoft is :", (age_16_bis + age_18_bis))

The number of games prohibited for children under 16/18 from Ubisoft is : 1


In [ ]:
age_df2 = dataset.select('data.publisher', 'data.name', 'data.required_age')
age_df2.createOrReplaceTempView('age_table')
ubisoft_table_age = spark.sql("SELECT * FROM age_table WHERE publisher IN ('Ubisoft') AND required_age BETWEEN 16 AND 18")
display(ubisoft_table_age)

publisher name required_age Ubisoft South Park: The Fractured But Whole 18

The only one game of Ubisoft with a required age is South Park: The Fractured But Whole.

In [ ]:
ubisoft_genre = fav_genre_df.filter(fav_genre_df["publisher"] == "Ubisoft")
display(ubisoft_genre)

publisher genre count publisher_count genre_per_publisher_% Ubisoft Action 70 221 31.67420814479638 Ubisoft Adventure 45 221 20.361990950226243 Ubisoft Strategy 22 221 9.95475113122172 Ubisoft RPG 19 221 8.597285067873303 Ubisoft Simulation 18 221 8.144796380090497 Ubisoft Racing 14 221 6.334841628959276 Ubisoft Casual 11 221 4.97737556561086 Ubisoft Indie 7 221 3.167420814479638 Ubisoft Free to Play 6 221 2.7149321266968327 Ubisoft Sports 5 221 2.262443438914027 Ubisoft Massively Multiplayer 4 221 1.8099547511312217

Databricks visualization. Run in Databricks to view.

The games that Ubisoft publish are mainly from 2 genres : first Action games (31.7%), and second Adventure games (20.4%). All other genres represent less than 10% of the games Ubisoft have published.

In [ ]:
platform_ubisoft_df = dataset.select('data.publisher', 'data.platforms.linux', 'data.platforms.mac', 'data.platforms.windows')
platform_ubisoft_df = platform_ubisoft_df.withColumn("linux", platform_ubisoft_df.linux.cast("int")).withColumn("mac", platform_ubisoft_df.mac.cast("int"))\
    .withColumn("windows", platform_ubisoft_df.windows.cast("int"))
platform_ubisoft_df.createOrReplaceTempView('platform_table')
ubisoft_table_platform = spark.sql("SELECT SUM(linux) AS linux, SUM(mac) AS mac, SUM(windows) AS windows FROM platform_table\
                                   WHERE publisher IN ('Ubisoft') GROUP BY publisher")
display(ubisoft_table_platform)

linux mac windows 2 6 127

Ubisoft has much more games published on windows (127) platform than mac or linux (6 & 2).

In [ ]:
dataset.printSchema()

root
 |-- data: struct (nullable = true)
 |    |-- appid: long (nullable = true)
 |    |-- categories: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- ccu: long (nullable = true)
 |    |-- developer: string (nullable = true)
 |    |-- discount: string (nullable = true)
 |    |-- genre: string (nullable = true)
 |    |-- header_image: string (nullable = true)
 |    |-- initialprice: string (nullable = true)
 |    |-- languages: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- negative: long (nullable = true)
 |    |-- owners: string (nullable = true)
 |    |-- platforms: struct (nullable = true)
 |    |    |-- linux: boolean (nullable = true)
 |    |    |-- mac: boolean (nullable = true)
 |    |    |-- windows: boolean (nullable = true)
 |    |-- positive: long (nullable = true)
 |    |-- price: string (nullable = true)
 |    |-- publisher: string (nullable = true)
 |    |-- release_date: string (nullable = true)
 |    |-

### Conclusion

We better understand the video game market with this analysis. \

There are major players in the industry, and Ubisoft is one of them as his ninth place in games produced for publishers show us. The best rated games is Aventura Copilului Albastru și Urât. The Covid had an effect in publishing games, there were more games produced during this period. Games are not often discounted and the price distribution is really wide, starting with free games and ending with a 99 900 $ game. Biggest part of games in English. There are only 261 games prohibited for children under.\

The main genres of published games are Indie, followed by Action, Casual and Adventure, which are also the most lucrative genres. Most of publishers has favorite genres, and Ubisoft too with Action and Adventure games. There are no genre with negative ratio.\

There are much more games available on Windows than Mac or Linux, and its for all genres.\

We can conclude that there are some factors affecting the popularity of a video game such as : the genre(s) selected for the game (some genres perform better), the date of release (Covid was a good period), platform availability (they have to publish their games on windows at least), and of course users ratings (ratings are always important in customers decisions).

In [ ]:
# Link to Databricks :
"https://databricks-prod-cloudfront.cloud.databricks.com/public/4027ec902e239c93eaaa8714f173bcfc/5035187331693614/3660298204496309/4781049071055596/latest.html"